In [1]:
from ase_interface import ANIENS
from ase_interface import ensemblemolecule

import pyNeuroChem as pync
import pyaniasetools as pya
import hdnntools as hdt

import numpy as np
import  ase
import time
#from ase.build import molecule
#from ase.neb import NEB
#from ase.calculators.mopac import MOPAC
from ase.md.langevin import Langevin
from ase.md.verlet import VelocityVerlet
from ase.io.trajectory import Trajectory
from ase import units

from ase.md.velocitydistribution import MaxwellBoltzmannDistribution

from ase.optimize.fire import FIRE as QuasiNewton

from ase.md.nvtberendsen import NVTBerendsen
from ase.md import MDLogger

#from ase.neb import NEBtools
from ase.io import read, write
from ase.optimize import BFGS, LBFGS

import matplotlib
import matplotlib as mpl

import matplotlib.pyplot as plt

import seaborn as sns

van Der Waals correction will be unavailable. Please install ased3


In [2]:
dir = '/nh/nest/u/jsmith/scratch/Research/MD_TEST/pt/'

# Molecule file
molfile = dir + 'pt.xyz'
#molfile = dir + 'optmol.xyz'

# Dynamics file
xyzfile = dir + 'mdcrd.xyz'

# Trajectory file
trajfile = dir + 'traj.dat'

# Optimized structure out:
optfile = dir + 'optmol.xyz'

T = 300.0 # Temperature
dt = 0.25
C = 0.1 # Optimization convergence
steps = 100000

ntdir = '/nh/nest/u/jsmith/scratch/Gits/ANI-Networks/networks/ANI-TZ-9.0.4/'
cns = ntdir + 'rHCNO-4.6A_16-3.1A_a4-8.params'
sae = ntdir + 'sae_linfit.dat'
nnf = ntdir + 'train'
Nn = 5

In [3]:
# Load molecule
mol = read(molfile)
#L = 14.140479202201726
#mol.set_cell(([[L, 0, 0],
#               [0, L, 0],
#               [0, 0, L]]))

#mol.set_pbc((True, True, True))

In [4]:
# Set NC
aens = ensemblemolecule(cns, sae, nnf, Nn, 0)

# Set ANI calculator
mol.set_calculator(ANIENS(aens,sdmx=20000000.0))

In [5]:
def erg_rsix (Rmag):
    return np.power(Rmag,-4)

def frc_rsix (Rmag,R):
    F = 4.0*np.power(Rmag,-6)*R                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        
    return F

#mol.calc.set_pairwise(erg_rsix, frc_rsix)

In [6]:
# Optimize molecule
start_time = time.time()
dyn = QuasiNewton(mol)
dyn.run(fmax=C)
print('[ANI Total time:', time.time() - start_time, 'seconds]')

# Save optimized mol
spc = mol.get_chemical_symbols()
pos = mol.get_positions(wrap=False).reshape(1,len(spc),3)

hdt.writexyzfile(optfile, pos, spc)

      Step     Time          Energy         fmax
FIRE:    0 17:33:45   -22338.855536       15.6263
FIRE:    1 17:33:45   -22339.583097        4.5175
FIRE:    2 17:33:45   -22339.676278        4.0476
FIRE:    3 17:33:45   -22339.818963        2.9866
FIRE:    4 17:33:45   -22339.927338        1.0484
FIRE:    5 17:33:45   -22339.897998        2.9169
FIRE:    6 17:33:45   -22339.906906        2.6634
FIRE:    7 17:33:45   -22339.921674        2.2046
FIRE:    8 17:33:45   -22339.937702        1.6188
FIRE:    9 17:33:45   -22339.950801        0.9932
FIRE:   10 17:33:45   -22339.958725        0.4383
FIRE:   11 17:33:45   -22339.961889        0.7006
FIRE:   12 17:33:45   -22339.962874        1.0545
FIRE:   13 17:33:45   -22339.963228        1.0437
FIRE:   14 17:33:45   -22339.963929        1.0221
FIRE:   15 17:33:45   -22339.964955        0.9900
FIRE:   16 17:33:45   -22339.966281        0.9476
FIRE:   17 17:33:45   -22339.967868        0.8955
FIRE:   18 17:33:45   -22339.969678        0.8344
F

In [7]:
#MaxwellBoltzmannDistribution(mol, 2.0 * units.kB)

# We want to run MD with constant energy using the VelocityVerlet algorithm.
#dyn = NVTBerendsen(mol, 1 * units.fs, 100.0, taut=1.0*1000*units.fs)
# coefficient to 0.02 atomic units.
dyn = Langevin(mol, dt * units.fs, T * units.kB, 0.04)

In [8]:
# Open MD output
mdcrd = open(xyzfile,'w')

# Open MD output
traj = open(trajfile,'w')

# Define the printer
def storeenergy(a=mol, d=dyn, b=mdcrd, t=traj):  # store a reference to atoms in the definition.
    """Function to print the potential, kinetic and total energy."""
    epot = a.get_potential_energy() / len(a)
    ekin = a.get_kinetic_energy() / len(a)

    stddev =  hdt.evtokcal*a.calc.stddev

    t.write(str(d.get_number_of_steps()) + ' ' + str(ekin / (1.5 * units.kB)) + ' ' + str(epot) + ' ' + str(ekin) + ' ' + str(epot+ekin) + ' ' + str(stddev) + '\n')
    b.write(str(len(a)) + '\n' + str(ekin / (1.5 * units.kB)) + ' Step: ' + str(d.get_number_of_steps()) + '\n')
    c = a.get_positions()
    for j, i in zip(a, c):
        b.write(str(j.symbol) + ' ' + str(i[0]) + ' ' + str(i[1]) + ' ' + str(i[2]) + '\n')

    print('Step: %d Energy per atom: Epot = %.3f  Ekin = %.3f (T=%.3fK)  '
          'Etot = %.6f' ' StdDev = %.3f' % (d.get_number_of_steps(), epot, ekin, ekin / (1.5 * units.kB), epot + ekin, stddev))
dyn.attach(storeenergy, interval=25)

In [9]:
start_time = time.time()
dyn.run(1000000)
print('[ANI Total time:', time.time() - start_time, 'seconds]')

Step: 25 Energy per atom: Epot = -657.099  Ekin = 0.001 (T=8.602K)  Etot = -657.098242 StdDev = 1.956
Step: 50 Energy per atom: Epot = -657.099  Ekin = 0.003 (T=20.755K)  Etot = -657.096468 StdDev = 1.975
Step: 75 Energy per atom: Epot = -657.099  Ekin = 0.004 (T=27.376K)  Etot = -657.095142 StdDev = 1.936
Step: 100 Energy per atom: Epot = -657.097  Ekin = 0.005 (T=35.407K)  Etot = -657.092729 StdDev = 2.045
Step: 125 Energy per atom: Epot = -657.097  Ekin = 0.007 (T=50.335K)  Etot = -657.090709 StdDev = 2.060
Step: 150 Energy per atom: Epot = -657.097  Ekin = 0.008 (T=62.307K)  Etot = -657.089200 StdDev = 2.145
Step: 175 Energy per atom: Epot = -657.097  Ekin = 0.010 (T=74.017K)  Etot = -657.087061 StdDev = 1.922
Step: 200 Energy per atom: Epot = -657.097  Ekin = 0.011 (T=83.759K)  Etot = -657.085772 StdDev = 1.981
Step: 225 Energy per atom: Epot = -657.095  Ekin = 0.012 (T=92.560K)  Etot = -657.083522 StdDev = 2.001
Step: 250 Energy per atom: Epot = -657.097  Ekin = 0.015 (T=114.409K

Step: 1975 Energy per atom: Epot = -657.097  Ekin = 0.038 (T=290.378K)  Etot = -657.059319 StdDev = 1.442
Step: 2000 Energy per atom: Epot = -657.090  Ekin = 0.029 (T=227.410K)  Etot = -657.061002 StdDev = 1.239
Step: 2025 Energy per atom: Epot = -657.099  Ekin = 0.037 (T=287.845K)  Etot = -657.062026 StdDev = 1.668
Step: 2050 Energy per atom: Epot = -657.099  Ekin = 0.036 (T=279.936K)  Etot = -657.062481 StdDev = 2.013
Step: 2075 Energy per atom: Epot = -657.104  Ekin = 0.042 (T=328.399K)  Etot = -657.061832 StdDev = 1.984
Step: 2100 Energy per atom: Epot = -657.102  Ekin = 0.041 (T=315.721K)  Etot = -657.060932 StdDev = 1.614
Step: 2125 Energy per atom: Epot = -657.096  Ekin = 0.033 (T=256.876K)  Etot = -657.062886 StdDev = 1.254
Step: 2150 Energy per atom: Epot = -657.098  Ekin = 0.035 (T=269.887K)  Etot = -657.063461 StdDev = 1.155
Step: 2175 Energy per atom: Epot = -657.102  Ekin = 0.042 (T=322.446K)  Etot = -657.060531 StdDev = 0.969
Step: 2200 Energy per atom: Epot = -657.099  E

Step: 3925 Energy per atom: Epot = -657.110  Ekin = 0.034 (T=261.757K)  Etot = -657.076079 StdDev = 1.243
Step: 3950 Energy per atom: Epot = -657.106  Ekin = 0.030 (T=232.079K)  Etot = -657.076254 StdDev = 1.280
Step: 3975 Energy per atom: Epot = -657.106  Ekin = 0.027 (T=210.023K)  Etot = -657.078408 StdDev = 1.303
Step: 4000 Energy per atom: Epot = -657.104  Ekin = 0.027 (T=210.130K)  Etot = -657.077142 StdDev = 1.462
Step: 4025 Energy per atom: Epot = -657.106  Ekin = 0.027 (T=205.647K)  Etot = -657.079794 StdDev = 1.526
Step: 4050 Energy per atom: Epot = -657.110  Ekin = 0.030 (T=231.028K)  Etot = -657.080524 StdDev = 1.740
Step: 4075 Energy per atom: Epot = -657.109  Ekin = 0.026 (T=204.800K)  Etot = -657.082365 StdDev = 1.465
Step: 4100 Energy per atom: Epot = -657.109  Ekin = 0.029 (T=221.070K)  Etot = -657.080043 StdDev = 1.385
Step: 4125 Energy per atom: Epot = -657.102  Ekin = 0.024 (T=183.663K)  Etot = -657.078594 StdDev = 1.566
Step: 4150 Energy per atom: Epot = -657.105  E

Step: 5875 Energy per atom: Epot = -657.100  Ekin = 0.038 (T=290.926K)  Etot = -657.062042 StdDev = 1.871
Step: 5900 Energy per atom: Epot = -657.097  Ekin = 0.033 (T=252.542K)  Etot = -657.063975 StdDev = 1.983
Step: 5925 Energy per atom: Epot = -657.102  Ekin = 0.038 (T=296.869K)  Etot = -657.063776 StdDev = 1.573
Step: 5950 Energy per atom: Epot = -657.102  Ekin = 0.035 (T=272.363K)  Etot = -657.066934 StdDev = 2.123
Step: 5975 Energy per atom: Epot = -657.102  Ekin = 0.035 (T=272.151K)  Etot = -657.067279 StdDev = 2.388
Step: 6000 Energy per atom: Epot = -657.105  Ekin = 0.039 (T=302.541K)  Etot = -657.065498 StdDev = 1.979
Step: 6025 Energy per atom: Epot = -657.102  Ekin = 0.043 (T=332.214K)  Etot = -657.059552 StdDev = 1.651
Step: 6050 Energy per atom: Epot = -657.099  Ekin = 0.039 (T=303.171K)  Etot = -657.059760 StdDev = 1.809
Step: 6075 Energy per atom: Epot = -657.101  Ekin = 0.042 (T=324.370K)  Etot = -657.058728 StdDev = 1.255
Step: 6100 Energy per atom: Epot = -657.090  E

Step: 7825 Energy per atom: Epot = -657.098  Ekin = 0.035 (T=269.632K)  Etot = -657.063470 StdDev = 1.483
Step: 7850 Energy per atom: Epot = -657.108  Ekin = 0.046 (T=352.928K)  Etot = -657.062765 StdDev = 1.316
Step: 7875 Energy per atom: Epot = -657.108  Ekin = 0.045 (T=348.246K)  Etot = -657.062959 StdDev = 1.374
Step: 7900 Energy per atom: Epot = -657.110  Ekin = 0.047 (T=366.662K)  Etot = -657.062607 StdDev = 1.320
Step: 7925 Energy per atom: Epot = -657.107  Ekin = 0.044 (T=336.665K)  Etot = -657.063542 StdDev = 1.328
Step: 7950 Energy per atom: Epot = -657.108  Ekin = 0.045 (T=349.262K)  Etot = -657.062825 StdDev = 1.263
Step: 7975 Energy per atom: Epot = -657.105  Ekin = 0.044 (T=338.089K)  Etot = -657.061617 StdDev = 1.331
Step: 8000 Energy per atom: Epot = -657.101  Ekin = 0.039 (T=305.082K)  Etot = -657.061378 StdDev = 1.251
Step: 8025 Energy per atom: Epot = -657.104  Ekin = 0.042 (T=327.478K)  Etot = -657.061572 StdDev = 1.009
Step: 8050 Energy per atom: Epot = -657.100  E

...

Step: 991525 Energy per atom: Epot = -657.166  Ekin = 0.039 (T=302.186K)  Etot = -657.126843 StdDev = 0.398
Step: 991550 Energy per atom: Epot = -657.162  Ekin = 0.034 (T=263.620K)  Etot = -657.128124 StdDev = 0.274
Step: 991575 Energy per atom: Epot = -657.164  Ekin = 0.034 (T=262.477K)  Etot = -657.129900 StdDev = 0.321
Step: 991600 Energy per atom: Epot = -657.165  Ekin = 0.039 (T=298.025K)  Etot = -657.126218 StdDev = 0.323
Step: 991625 Energy per atom: Epot = -657.163  Ekin = 0.038 (T=295.111K)  Etot = -657.125322 StdDev = 0.233
Step: 991650 Energy per atom: Epot = -657.167  Ekin = 0.043 (T=329.544K)  Etot = -657.124543 StdDev = 0.314
Step: 991675 Energy per atom: Epot = -657.163  Ekin = 0.037 (T=284.151K)  Etot = -657.126289 StdDev = 0.293
Step: 991700 Energy per atom: Epot = -657.160  Ekin = 0.037 (T=289.376K)  Etot = -657.122856 StdDev = 0.259
Step: 991725 Energy per atom: Epot = -657.157  Ekin = 0.031 (T=236.595K)  Etot = -657.126565 StdDev = 0.354
Step: 991750 Energy per atom

Step: 993425 Energy per atom: Epot = -657.164  Ekin = 0.036 (T=278.606K)  Etot = -657.128209 StdDev = 0.434
Step: 993450 Energy per atom: Epot = -657.171  Ekin = 0.042 (T=324.824K)  Etot = -657.129201 StdDev = 0.281
Step: 993475 Energy per atom: Epot = -657.165  Ekin = 0.034 (T=264.321K)  Etot = -657.131303 StdDev = 0.297
Step: 993500 Energy per atom: Epot = -657.169  Ekin = 0.038 (T=292.842K)  Etot = -657.130726 StdDev = 0.409
Step: 993525 Energy per atom: Epot = -657.173  Ekin = 0.045 (T=345.060K)  Etot = -657.128732 StdDev = 0.389
Step: 993550 Energy per atom: Epot = -657.173  Ekin = 0.043 (T=333.105K)  Etot = -657.129695 StdDev = 0.359
Step: 993575 Energy per atom: Epot = -657.167  Ekin = 0.039 (T=305.412K)  Etot = -657.127801 StdDev = 0.461
Step: 993600 Energy per atom: Epot = -657.166  Ekin = 0.037 (T=289.301K)  Etot = -657.128506 StdDev = 0.434
Step: 993625 Energy per atom: Epot = -657.168  Ekin = 0.041 (T=315.750K)  Etot = -657.127146 StdDev = 0.367
Step: 993650 Energy per atom

Step: 995325 Energy per atom: Epot = -657.161  Ekin = 0.039 (T=299.770K)  Etot = -657.122050 StdDev = 0.430
Step: 995350 Energy per atom: Epot = -657.167  Ekin = 0.046 (T=358.146K)  Etot = -657.120486 StdDev = 0.287
Step: 995375 Energy per atom: Epot = -657.158  Ekin = 0.036 (T=278.098K)  Etot = -657.122204 StdDev = 0.424
Step: 995400 Energy per atom: Epot = -657.159  Ekin = 0.037 (T=284.151K)  Etot = -657.122609 StdDev = 0.387
Step: 995425 Energy per atom: Epot = -657.166  Ekin = 0.045 (T=346.421K)  Etot = -657.120911 StdDev = 0.289
Step: 995450 Energy per atom: Epot = -657.156  Ekin = 0.034 (T=262.204K)  Etot = -657.122246 StdDev = 0.274
Step: 995475 Energy per atom: Epot = -657.154  Ekin = 0.031 (T=240.220K)  Etot = -657.123140 StdDev = 0.255
Step: 995500 Energy per atom: Epot = -657.159  Ekin = 0.037 (T=285.492K)  Etot = -657.122379 StdDev = 0.391
Step: 995525 Energy per atom: Epot = -657.165  Ekin = 0.042 (T=323.003K)  Etot = -657.123479 StdDev = 0.434
Step: 995550 Energy per atom

Step: 997225 Energy per atom: Epot = -657.159  Ekin = 0.035 (T=266.914K)  Etot = -657.124711 StdDev = 0.374
Step: 997250 Energy per atom: Epot = -657.168  Ekin = 0.043 (T=330.318K)  Etot = -657.125769 StdDev = 0.331
Step: 997275 Energy per atom: Epot = -657.164  Ekin = 0.043 (T=333.190K)  Etot = -657.121196 StdDev = 0.343
Step: 997300 Energy per atom: Epot = -657.160  Ekin = 0.040 (T=310.089K)  Etot = -657.119632 StdDev = 0.409
Step: 997325 Energy per atom: Epot = -657.167  Ekin = 0.046 (T=355.273K)  Etot = -657.121141 StdDev = 0.256
Step: 997350 Energy per atom: Epot = -657.162  Ekin = 0.038 (T=297.406K)  Etot = -657.123375 StdDev = 0.428
Step: 997375 Energy per atom: Epot = -657.162  Ekin = 0.037 (T=287.040K)  Etot = -657.124671 StdDev = 0.379
Step: 997400 Energy per atom: Epot = -657.164  Ekin = 0.043 (T=329.122K)  Etot = -657.121250 StdDev = 0.340
Step: 997425 Energy per atom: Epot = -657.162  Ekin = 0.041 (T=316.829K)  Etot = -657.120954 StdDev = 0.432
Step: 997450 Energy per atom

Step: 999125 Energy per atom: Epot = -657.162  Ekin = 0.039 (T=304.803K)  Etot = -657.122301 StdDev = 0.277
Step: 999150 Energy per atom: Epot = -657.158  Ekin = 0.034 (T=262.086K)  Etot = -657.124007 StdDev = 0.289
Step: 999175 Energy per atom: Epot = -657.168  Ekin = 0.045 (T=346.170K)  Etot = -657.122818 StdDev = 0.169
Step: 999200 Energy per atom: Epot = -657.170  Ekin = 0.048 (T=369.950K)  Etot = -657.122000 StdDev = 0.254
Step: 999225 Energy per atom: Epot = -657.160  Ekin = 0.035 (T=274.488K)  Etot = -657.124811 StdDev = 0.199
Step: 999250 Energy per atom: Epot = -657.169  Ekin = 0.043 (T=334.196K)  Etot = -657.125539 StdDev = 0.187
Step: 999275 Energy per atom: Epot = -657.170  Ekin = 0.042 (T=325.249K)  Etot = -657.127651 StdDev = 0.285
Step: 999300 Energy per atom: Epot = -657.165  Ekin = 0.037 (T=289.680K)  Etot = -657.127155 StdDev = 0.331
Step: 999325 Energy per atom: Epot = -657.168  Ekin = 0.039 (T=300.214K)  Etot = -657.129056 StdDev = 0.190
Step: 999350 Energy per atom